In [1]:
import os
import numpy as np
import pandas as pd
import statistics
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
path = os.getcwd()

In [2]:
def load(fname):
    f = open(fname,'r')

    data = []
    for line in f.readlines():
        data.append(line.replace('\n',''))

    f.close()

    return data

In [10]:
def get_data(directories_in_curdir, algorithms):
    data = {}
    problem_params = {}
    for i in range(0, len(directories_in_curdir)):        
        folder = path + "\\" + directories_in_curdir[i]
        files = ()    
        for file in os.listdir(folder):
            if file.endswith(".txt"):
                if file.startswith("full global result"):
                    files = files + (file,)  
        for f in files:
            file = folder + "\\" + f
            loaded_data = load(file)
            problem  = loaded_data[0]
            runamount = loaded_data[2]
            individualsAmount = loaded_data[3]
            iterationsAmount = loaded_data[4]
            for k in range(0, 6):
                loaded_data.pop(0)                
            if problem not in data:
                data[problem] = {}                
            if algorithms[i] == 'ScRGA':
                loaded_data = [loaded_data[0]]            
            data[problem][algorithms[i]] = loaded_data                            
            if problem not in problem_params:
                problem_params[problem] = {'runamount': runamount, 'individualsAmount': individualsAmount, 'iterationsAmount': iterationsAmount}
            else:
                if problem_params[problem]['individualsAmount'] != individualsAmount:
                    print("ERROR for " + problem + ". Individuals amount = " + problem_params[problem]['individualsAmount'])
                    print("but for algorithm " + algorithms[i] + " it is " + individualsAmount)
                if problem_params[problem]['iterationsAmount'] != iterationsAmount:
                    print("ERROR for " + problem + ". Iterations amount = " + problem_params[problem]['iterationsAmount'])
                    print("but for algorithm " + algorithms[i] + " it is " + iterationsAmount)
    return data, problem_params

In [3]:
def process_data(data):
    processed_data = {}
    for problem in data:
        processed_data[problem] = {}
        for alg in data[problem]:
            processed_data[problem][alg] = []
            for s in data[problem][alg]:
                res_list = s.split('\t')
                processed_data[problem][alg].append(float(res_list[len(res_list) - 1]))
    mean_data = {}
    best_data = {}
    std_data = {}
    for problem in processed_data:
        mean_data[problem] = {}
        best_data[problem] = {}
        std_data[problem] = {}
        for alg in processed_data[problem]:
            mean_data[problem][alg] = statistics.mean(processed_data[problem][alg])
            best_data[problem][alg] = max(processed_data[problem][alg])
            if len(processed_data[problem][alg]) > 1:
                std_data[problem][alg] = statistics.stdev(processed_data[problem][alg])
            else:
                std_data[problem][alg] = 0
    return processed_data, mean_data, best_data, std_data

In [4]:
def average_data(mean_data, problems, algorithms):
    result = {}
    for alg in algorithms:
        res = 0
        count = 0
        for problem in problems:
            if alg in mean_data[problem]:
                res += mean_data[problem][alg]
                count += 1
        result[alg] = res / count
    return result

In [5]:
def average_and_best_data(mean_data, best_data, problems, algorithms):
    avg_data = average_data(mean_data, problems, algorithms)

    for alg in algorithms:
        if 'Sc' not in alg:
            res = 0
            count = 0
            for prob in problems:
                if alg in best_data[prob]:
                    res += best_data[prob][alg]
                    count += 1
            avg_data[alg + " best"] = res / count
    return avg_data

In [6]:
def make_mean_df_for_problem(problem, mean_data, best_data, algorithms, sorted_extended_algorithms):
    df = pd.DataFrame(index = sorted_extended_algorithms)
    df["mean"] = pd.Series(mean_data[problem])
    for alg in algorithms:
        if 'Sc' not in alg:
            df.loc[alg + ' best', 'mean'] = best_data[problem][alg]
            #df = df.append({'algorithm' : alg + ' best', 'mean' : best_data[problem][alg]}, ignore_index=True)
    df = df.reset_index().rename({'index':'algorithm'}, axis = 'columns')
    return df

In [8]:
directories_in_curdir = list(filter(os.path.isdir, os.listdir(os.curdir)))
directories_in_curdir.pop(0)
algorithms = [x.replace("Real ", "") for x in directories_in_curdir]

In [11]:
data, problem_params = get_data(directories_in_curdir, algorithms)

In [12]:
problems = ['Problem 0', 'Problem 1', 'Problem 2', 'Problem 3', 'Problem 4', 'Problem 5', 'Problem 6', 'Problem 7',
            'Problem 8', 'Problem 9', 'Problem 10', 'Problem 11', 'Problem 12', 'Problem 13', 'Problem 14', 'Problem 15',
            'Problem 16', 'Problem 17', 'Problem 18', 'Problem 19', 'Problem 20', 'Problem 21', 'Problem 22', 'Problem 23']
problems_1 = ['Problem 0', 'Problem 1', 'Problem 2', 'Problem 3', 'Problem 4', 'Problem 5', 'Problem 6', 'Problem 7',
            'Problem 8', 'Problem 9', 'Problem 10', 'Problem 11', 'Problem 12', 'Problem 13']
problems_2 = ['Problem 14', 'Problem 15', 'Problem 16', 'Problem 17', 'Problem 18', 'Problem 19', 
              'Problem 20', 'Problem 21', 'Problem 22', 'Problem 23']

In [15]:
processed_data, mean_data, best_data, std_data = process_data(data)
averaged_data = average_and_best_data(mean_data, best_data, problems, algorithms)

In [33]:
extended_algorithms = [x for x in averaged_data.keys()]
extended_algorithms.sort()

In [34]:
sorted_extended_algorithms = ['PSO', 'ScPSO', 'PSO best', 'RGA', 'ScRGA', 'RGA best', 'DE', 'ScDE', 'DE best', 
                             'ScCCreal SBSP', 'ScCCreal BtA BrW', 'ScCCreal BtA BrR',
                              'ScCCreal BtA RrW', 'ScCCreal BtA RrR', 'ScCCreal AtA BrW', 'ScCCreal AtA BrR',
                              'ScCCreal AtA RrW', 'ScCCreal AtA RrR']
sorted_short_algorithms = ['PSO', 'PSO best', 'RGA', 'RGA best', 'DE', 'DE best']

In [35]:
def add_br(s):
    if 'ScCCreal' in s:
        res_list = s.split('ScCCreal')
        return 'ScCCreal' + "<br>" + res_list[1]
    if 'best' in s:
        res_list = s.split('best')
        return res_list[0] + "<br>" + 'best'
    return s

In [36]:
patterns = ('', '/', '\\', 'x', '-', '|', '+', '.', '', '/', '\\', 'x', '-', '|', '+', '.', 
            '', '/', '\\', 'x', '-', '|', '+', '.')

In [37]:
def apply_style(fig, width=700, height=400, range=[0.8, 1]):
    fig.update_xaxes(tickangle=90)
    fig.update_layout(autosize=False, width=width, height=height, showlegend=False, 
        font=dict(family="Times New Roman", size=20, color='black'),
                 template="plotly_white"
    )
    fig.update_xaxes(title='', showline=True, linewidth=1, linecolor='black')
    fig.update_yaxes(title='', showline=True, linewidth=1, linecolor='black', gridcolor='lightgray')
    fig.update_traces(marker_pattern_size=6, marker_line_color='black')
    fig.update_yaxes(range=range)
    fig.update_annotations(font_size=18)

In [67]:
def make_bar_plot(data, width=700, height=400, color=True, range=[0.8, 1]):
    if color:
        color_discrete_sequence = px.colors.sequential.Viridis
    else:
        color_discrete_sequence = px.colors.sequential.Greys
    fig = px.bar(data, x="algorithm", y='mean', color="algorithm", labels={'value':'reliability'}, 
             color_discrete_sequence=color_discrete_sequence, text_auto=True, width=width, height=height,
             pattern_shape="index", pattern_shape_sequence=patterns)
    apply_style(fig, width, height, range)
    return fig

In [75]:
df = pd.DataFrame(index = sorted_extended_algorithms)
df["mean"] = pd.Series(averaged_data)
df["mean"] = round(df["mean"], 3)
df = df.reset_index().rename({'index':'algorithm'}, axis = 'columns')
df["algorithm"] = df["algorithm"].apply(lambda x: add_br(x))
df = df.reset_index().rename({'index':'index'}, axis = 'columns')
fig = make_bar_plot(df, width=900, height=500, color=True, range=[0, 1])
fig.show()

In [77]:
averaged_data_short = {}
for x in sorted_short_algorithms:
    averaged_data_short[x] = averaged_data[x]
df_short = pd.DataFrame(index = sorted_short_algorithms)
df_short["mean"] = pd.Series(averaged_data_short)
df_short["mean"] = round(df_short["mean"], 3)
df_short = df_short.reset_index().rename({'index':'algorithm'}, axis = 'columns')
df_short["algorithm"] = df_short["algorithm"].apply(lambda x: add_br(x))
df_short = df_short.reset_index().rename({'index':'index'}, axis = 'columns')

In [79]:
make_bar_plot(df_short, width=700, height=400, color=True, range=[0, 1])

In [80]:
make_bar_plot(df_short, width=700, height=400, color=False, range=[0, 1])

In [83]:
fig = make_subplots(rows=12, cols=2, subplot_titles=problems)
count_x = 0
couny_y = 0
count = 0
for problem in problems:
    if count % 2 == 1:
        count_y = 2
    else:
        count_y = 1
        count_x += 1
    df = make_mean_df_for_problem(problem, mean_data, best_data, algorithms, sorted_extended_algorithms)
    df = df.reset_index().rename({'index':'index'}, axis = 'columns')
    df['mean'] = df['mean'].round(decimals = 3)
    fig.add_trace(go.Bar(x=df['algorithm'], y=df['mean'], text=df['mean'],
                         marker=dict(color = df['index'], colorscale='viridis')), 
                  count_x, count_y)
    count = count + 1

fig.update_traces(marker_pattern_shape=patterns)
apply_style(fig, 1200, 5000, [0,1])

fig.show()

In [37]:
problem = problems[9]

Problem 9


In [84]:
def get_params_plot(algorithm, scalg, problem, processed_data, range=[0.1, 1]):
    df_for_alg = pd.DataFrame(processed_data[problem][algorithm])
    df_for_alg = df_for_alg.reset_index().rename({'index':'index'}, axis = 'columns')
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df_for_alg['index'], y=df_for_alg[0],mode='markers', name=algorithm, 
                             marker=dict(color=df_for_alg[0], colorscale='viridis')))
    fig.add_trace(go.Scatter(x=df_for_alg['index'], y=processed_data[problem][scalg]*len(df_for_alg),  mode='lines', name=scalg,
                            line=dict(color='rgb(201, 2, 66)', width=2, dash='dash')))
    fig.update_layout(title={'text': problem, 'x':0.5, 'y':0.83}, width=600, height=400, showlegend=True, template="plotly_white",
                      font=dict(family="Times New Roman", size=20, color='black'))
    fig.update_yaxes(range=range, showline=True, linewidth=1, linecolor='black', gridcolor='lightgray')
    fig.update_xaxes(title='', showline=True, linewidth=1, linecolor='black')
    fig.update_yaxes(showline=True, linewidth=1, linecolor='black', gridcolor='lightgray')
    return fig

def show_params_plot(algorithm, scalg, problem, processed_data, range=[0.1, 1]):
    get_params_plot(algorithm, scalg, problem, processed_data, range).show()

In [85]:
show_params_plot('PSO', 'ScPSO', 'Problem 11', processed_data)

In [86]:
show_params_plot('RGA', 'ScRGA', 'Problem 11', processed_data)

In [87]:
show_params_plot('DE', 'ScDE', 'Problem 11', processed_data)

In [88]:
def add_params_plot_to_fig(fig, algorithm, scalg, problem, processed_data, count_x, count_y):
    df_for_alg = pd.DataFrame(processed_data[problem][algorithm])
    df_for_alg = df_for_alg.reset_index().rename({'index':'index'}, axis = 'columns')
    fig.add_trace(go.Scatter(x=df_for_alg['index'], y=df_for_alg[0],mode='markers', name=algorithm, 
                             marker=dict(color=df_for_alg[0], colorscale='viridis')), count_x, count_y)
    fig.add_trace(go.Scatter(x=df_for_alg['index'], y=processed_data[problem][scalg]*len(df_for_alg),  mode='lines', name=scalg,
                            line=dict(color='rgb(201, 2, 66)', width=2, dash='dash')), count_x, count_y)

In [93]:
def get_params_plot_for_problems(algorithm, scalg, range=[0.1, 1]):
    fig = make_subplots(rows=12, cols=2, subplot_titles=problems)
    count_x = 0
    couny_y = 0
    count = 0
    for problem in problems:
        if count % 2 == 1:
            count_y = 2
        else:
            count_y = 1
            count_x += 1
        add_params_plot_to_fig(fig, algorithm, scalg, problem, processed_data, count_x, count_y)
        count = count + 1

    fig.update_yaxes(range=range)
    fig.update_layout(autosize=False, width=1000, height=4000, showlegend=False, 
                      template="plotly_white", font=dict(family="Times New Roman", size=20, color='black'))
    fig.update_yaxes(showline=True, linewidth=1, linecolor='black', gridcolor='lightgray')
    fig.update_xaxes(title='', showline=True, linewidth=1, linecolor='black')
    fig.update_annotations(font_size=20)
    return fig

In [95]:
get_params_plot_for_problems('PSO', 'ScPSO')

In [96]:
get_params_plot_for_problems('RGA', 'ScRGA')

In [97]:
get_params_plot_for_problems('DE', 'ScDE')

In [99]:
def get_clean_data(data):  
    processed_data = {}
    for problem in data:
        processed_data[problem] = {}
        for alg in data[problem]:
            if alg in ['PSO', 'RGA', 'DE']:
                processed_data[problem][alg] = []
                for s in data[problem][alg]:
                    res_list = s.split('\t')
                    if alg == 'PSO':
                        dict_param = {'socialParameter':res_list[0], 'cognitiveParameter':res_list[1], 'w':res_list[2], 
                                      'effectiveness':float(res_list[-1])}
                        processed_data[problem][alg].append(dict_param)
                    elif alg == 'DE':
                        dict_param = {'DEType':res_list[0], 'CR':res_list[1], 
                                      'FF':res_list[2], 'lymbda':res_list[3], 
                                      'effectiveness':float(res_list[-1])}
                        if dict_param['DEType'] == 'РЎ РёСЃРїРѕР»СЊР·РѕРІР°РЅРёРµРј Р»СѓС‡С€РµРіРѕ РІРµРєС‚РѕСЂР°':
                            dict_param['DEType'] = 'С использованием лучшего вектора'
                        if dict_param['DEType'] == 'РЎ РёСЃРїРѕР»СЊР·РѕРІР°РЅРёРµРј С‚СЂРµС… СЃР»СѓС‡Р°Р№РЅС‹С… РІРµРєС‚РѕСЂРѕРІ':
                            dict_param['DEType'] = 'С использованием трех случайных векторов'
                        processed_data[problem][alg].append(dict_param)
                    else:
                        processed_data[problem][alg].append(res_list)
        
    return processed_data

In [100]:
clean_data = get_clean_data(data)

In [101]:
socialParameters = {'0.25':0, '0.5':1, '0.75':2, '1.0':3, '1.25':4, '1.5':5, '1.8':6, '2.0':7}
cognitiveParameters = {'0.25':0, '0.5':1, '0.75':2, '1.0':3, '1.25':4, '1.5':5, '1.8':6, '2.0':7}
ws = {'0.5':0, '0.6':1, '0.7':2, '0.8':3, '0.9':4, '1.0':5}

In [102]:
def get_PSO_matrix(problem):
    matrix = []
    for i in range(0,8):
        m = [0 for x in range(0, 6*8)]
        matrix.append(m)

    for count in range(0,384):
        socialParameter = clean_data[problem]['PSO'][count]['socialParameter']
        cognitiveParameter = clean_data[problem]['PSO'][count]['cognitiveParameter']
        w = clean_data[problem]['PSO'][count]['w']
        l = socialParameters[socialParameter]
        n = 6 * cognitiveParameters[cognitiveParameter] + ws[w]
        matrix[l][n] = float(clean_data[problem]['PSO'][count]['effectiveness'])
    return matrix

In [103]:
x_names_PSO = ['cp=0.25, w=0.5', 'cp=0.25, w=0.6', 'cp=0.25, w=0.7', 'cp=0.25, w=0.8', 'cp=0.25, w=0.9', 'cp=0.25, w=1.0',
           'cp=0.5, w=0.5', 'cp=0.5, w=0.6', 'cp=0.5, w=0.7', 'cp=0.5, w=0.8', 'cp=0.5, w=0.9', 'cp=0.5, w=1.0',
           'cp=0.75, w=0.5', 'cp=0.75, w=0.6', 'cp=0.75, w=0.7', 'cp=0.75, w=0.8', 'cp=0.75, w=0.9', 'cp=0.75, w=1.0',
           'cp=1.0, w=0.5', 'cp=1.0, w=0.6', 'cp=1.0, w=0.7', 'cp=1.0, w=0.8', 'cp=1.0, w=0.9', 'cp=1.0, w=1.0',
           'cp=1.25, w=0.5', 'cp=1.25, w=0.6', 'cp=1.25, w=0.7', 'cp=1.25, w=0.8', 'cp=1.25, w=0.9', 'cp=1.25, w=1.0',
           'cp=1.5, w=0.5', 'cp=1.5, w=0.6', 'cp=1.5, w=0.7', 'cp=1.5, w=0.8', 'cp=1.5, w=0.9', 'cp=1.5, w=1.0',
           'cp=1.8, w=0.5', 'cp=1.8, w=0.6', 'cp=1.8, w=0.7', 'cp=1.8, w=0.8', 'cp=1.8, w=0.9', 'cp=1.8, w=1.0',
           'cp=2.0, w=0.5', 'cp=2.0, w=0.6', 'cp=2.0, w=0.7', 'cp=2.0, w=0.8', 'cp=2.0, w=0.9', 'cp=2.0, w=1.0']
y_names_PSO = ['sp=0.25', 'sp=0.5', 'sp=0.75', 'sp=1.0', 'sp=1.25', 'sp=1.5', 'sp=1.8', 'sp=2.0']

In [104]:
problem = 'Problem 23'
matrix = get_PSO_matrix(problem)

fig = px.imshow(matrix, color_continuous_scale='viridis',
                x=x_names_PSO, y=y_names_PSO, height = 300, width=1000)
fig.update_layout(title={'text': problem, 'x':0.5, 'y':0.92})
fig.show()

In [105]:
matrices = []
for problem in problems:
    matrices.append(get_PSO_matrix(problem))

avg_matrix = []
for i in range(0,8):
    m = [0 for x in range(0, 48)]
    avg_matrix.append(m)

for i in range(0,8):
    for j in range(0,48):
        for m in range(0, len(matrices)):
            avg_matrix[i][j] = avg_matrix[i][j] + matrices[m][i][j]/float(len(matrices))

In [106]:
fig = px.imshow(avg_matrix, color_continuous_scale='viridis',
                x=x_names_PSO, y=y_names_PSO, height = 300, width=1000)
fig.update_layout(title={'text': 'Average on problems 0-23', 'x':0.5, 'y':0.94})
fig.show()

In [107]:
DETypes = {'С использованием лучшего вектора':0, 'С использованием трех случайных векторов':1}
CRs = {'0.3':0, '0.5':1, '0.7':2, '0.9':3, '1.0':4}
FFs = {'0.2':0, '0.5':1, '0.7':2, '1.0':3, '1.5':4}
lymbdas = {'0.2':0, '0.5':1, '0.7':2, '1.0':3, '1.5':4}

In [108]:
def get_DE_matrix(problem):
    matrix = []
    for i in range(0,6):
        m = [0 for x in range(0, 25)]
        matrix.append(m)

    for count in range(0,150):
        DEType = clean_data[problem]['DE'][count]['DEType']
        CR = clean_data[problem]['DE'][count]['CR']
        FF = clean_data[problem]['DE'][count]['FF']
        lymbda = clean_data[problem]['DE'][count]['lymbda']
        
        l = 0
        if DEType == 'С использованием трех случайных векторов':
            l = 0
        else:
            l = 1 + lymbdas[lymbda]
        
        n = 5 * CRs[CR] + FFs[FF]
        
        matrix[l][n] = float(clean_data[problem]['DE'][count]['effectiveness'])
    return matrix

In [109]:
x_names_DE = ['C=0.3, F=0.2', 'C=0.3, F=0.5', 'C=0.3, F=0.7', 'C=0.3, F=1.0', 'C=0.3, F=1.5',
              'C=0.5, F=0.2', 'C=0.5, F=0.5', 'C=0.5, F=0.7', 'C=0.5, F=1.0', 'C=0.5, F=1.5',
              'C=0.7, F=0.2', 'C=0.7, F=0.5', 'C=0.7, F=0.7', 'C=0.7, F=1.0', 'C=0.7, F=1.5',
              'C=0.9, F=0.2', 'C=0.9, F=0.5', 'C=0.9, F=0.7', 'C=0.9, F=1.0', 'C=0.9, F=1.5',
              'C=1.0, F=0.2', 'C=1.0, F=0.5', 'C=1.0, F=0.7', 'C=1.0, F=1.0', 'C=1.0, F=1.5']

y_names_DE = ['3 rand vect', 'best vect l=0.2', 'best vect l=0.5', 'best vect l=0.7', 'best vect l=1.0', 'best vect l=1.5']

In [110]:
problem = 'Problem 23'
matrix = get_DE_matrix(problem)

fig = px.imshow(matrix, color_continuous_scale='viridis',
                x=x_names_DE, y=y_names_DE, height = 300, width=600)
fig.update_layout(title={'text': problem, 'x':0.5, 'y':0.92})
fig.show()

In [111]:
def get_data_GA(directories_in_curdir):
    data = {}
    problem_params = {}

    folder = path + "\\" + 'RGA'
    files = ()    
    for file in os.listdir(folder):
        if file.endswith(".txt"):
            if file.startswith("global result table"):
                files = files + (file,)  
    for f in files:
        file = folder + "\\" + f
        loaded_data = load(file)
        problem  = loaded_data[0]
        for k in range(0, 57):
            loaded_data.pop(0)

        if problem not in data:
            data[problem] = {}

        data[problem] = loaded_data
    return data

In [112]:
def decode_ga_data(ga_data):
    gapar = {}
    for prob in ga_data:
        gapar[prob] = []
        for i in range(0,len(ga_data[prob])):
            ga_data[prob][i] = ga_data[prob][i].split('\t')
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][2][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][2][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][2][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][2][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][2][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][3][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][3][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][3][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][3][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][3][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][4][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][4][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][4][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][4][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][4][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][5][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][5][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][5][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][5][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][5][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][6][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][6][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][6][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][6][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][6][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][7][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][7][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][7][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][7][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][7][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][8][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][8][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][8][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][8][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][8][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][9][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][9][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][9][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][9][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][9][9]})
        
        
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][10][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][10][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][10][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][10][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][10][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][11][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][11][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][11][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][11][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][11][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][12][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][12][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][12][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][12][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][12][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][13][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][13][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][13][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][13][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][13][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][14][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][14][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][14][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][14][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][14][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][15][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][15][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][15][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][15][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][15][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][16][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][16][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][16][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][16][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][16][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][17][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][17][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][17][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][17][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][17][9]})
        
        
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][18][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][18][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][18][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][18][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][18][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][19][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][19][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][19][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][19][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][19][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][20][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][20][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][20][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][20][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][20][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][21][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][21][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][21][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][21][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][21][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][22][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][22][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][22][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][22][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][22][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][23][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][23][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][23][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][23][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][23][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][24][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][24][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][24][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][24][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][16][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'оч низ', 'el':'с элит', 'res':ga_data[prob][25][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'низ', 'el':'с элит', 'res':ga_data[prob][25][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'сред', 'el':'с элит', 'res':ga_data[prob][25][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'выс', 'el':'с элит', 'res':ga_data[prob][25][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'оч выс', 'el':'с элит', 'res':ga_data[prob][25][9]})
        
        
        
        
        
        
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][28][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][28][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][28][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][28][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 2', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][28][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][29][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][29][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][29][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][29][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 4', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][29][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][30][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][30][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][30][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][30][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'тур 8', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][30][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][31][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][31][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][31][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][31][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'проп', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][31][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][32][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][32][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][32][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][32][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг лин', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][32][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][33][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][33][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][33][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][33][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.95', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][33][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][34][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][34][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][34][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][34][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.9', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][34][9]})
        
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][35][5]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][35][6]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][35][7]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][35][8]})
        gapar[prob].append({'recomb': "равн", 'sel':'ранг эксп 0.8', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][35][9]})
        
        
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][36][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][36][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][36][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][36][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 2', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][36][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][37][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][37][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][37][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][37][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 4', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][37][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][38][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][38][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][38][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][38][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'тур 8', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][38][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][39][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][39][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][39][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][39][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'проп', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][39][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][40][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][40][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][40][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][40][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг лин', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][40][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][41][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][41][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][41][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][41][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.95', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][41][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][42][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][42][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][42][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][42][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.9', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][42][9]})
        
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][43][5]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][43][6]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][43][7]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][43][8]})
        gapar[prob].append({'recomb': "однтч", 'sel':'ранг эксп 0.8', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][43][9]})
        
        
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][44][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][44][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][44][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][44][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 2', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][44][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][45][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][45][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][45][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][45][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 4', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][45][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][46][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][46][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][46][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][46][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'тур 8', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][46][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][47][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][47][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][47][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][47][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'проп', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][47][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][48][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][48][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][48][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][48][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг лин', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][48][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][49][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][49][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][49][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][49][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.95', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][49][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][50][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][50][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][50][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][50][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.9', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][50][9]})
        
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'оч низ', 'el':'без элит', 'res':ga_data[prob][51][5]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'низ', 'el':'без элит', 'res':ga_data[prob][51][6]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'сред', 'el':'без элит', 'res':ga_data[prob][51][7]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'выс', 'el':'без элит', 'res':ga_data[prob][51][8]})
        gapar[prob].append({'recomb': "двутч", 'sel':'ранг эксп 0.8', 'mut':'оч выс', 'el':'без элит', 'res':ga_data[prob][51][9]})
        
    return gapar

In [113]:
ga_data = get_data_GA(directories_in_curdir)
ga_data_by_params = decode_ga_data(ga_data)

In [114]:
recombs = {'равн':0, 'однтч':1, 'двутч':1} #3
sels = {'тур 2':0, 'тур 4':1, 'тур 8':2, 'проп':3, 'ранг лин':4, 'ранг эксп 0.8':5, 'ранг эксп 0.9':6, 'ранг эксп 0.95':7} #8
muts = {'оч низ':0, 'низ':1, 'сред':2, 'выс':3, 'оч выс':4} #5
els = {'с элит':0, 'без элит':1} #2

In [115]:
def get_RGA_matrix(problem, ga_data_by_params):
    matrix = []
    for i in range(0,6):
        m = [0 for x in range(0, 40)]
        matrix.append(m)

    for count in range(0,240):
        recomb = ga_data_by_params[problem][count]['recomb']
        sel = ga_data_by_params[problem][count]['sel']
        mut = ga_data_by_params[problem][count]['mut']
        el = ga_data_by_params[problem][count]['el']
               
        l = 3 * els[el] + recombs[recomb]
        
        n = 5 * sels[sel] + muts[mut]
        
        matrix[l][n] = float(ga_data_by_params[problem][count]['res'])
    return matrix

In [116]:
x_names_RGA = []
for sel in sels.keys():
    for mut in muts.keys():
        x_names_RGA.append(sel + " " + mut)
y_names_RGA = []
for el in els.keys():
    for recomb in recombs.keys():
        y_names_RGA.append(el + " " + recomb)

In [118]:
problem = 'Problem 11'
matrix = get_RGA_matrix(problem, ga_data_by_params)
fig = px.imshow(matrix, color_continuous_scale='viridis',
                x=x_names_RGA, y=y_names_RGA, height = 400, width=900)
fig.update_layout(title={'text': problem, 'x':0.5, 'y':0.92})
fig.show()

In [136]:
def apply_style_lines(width=850, height=450, xaxis_title="Iteration", yaxis_title="Probability"):
    fig.update_layout(autosize=False, width=width, height=height, showlegend=True, xaxis_title=xaxis_title, 
                      yaxis_title=yaxis_title, template="plotly_white", 
                      font=dict(family="Times New Roman", size=18, color='black'))
    fig.update_xaxes(showline=True, linewidth=1, linecolor='black')
    fig.update_yaxes(showline=True, linewidth=1, linecolor='black', gridcolor='lightgray')
    fig.update_traces( marker_line_color='black')    

In [143]:
def parse_result_data(name):
    file = path + "\\" + name
    loaded_data = load(file)
    loaded_data.pop(0)
    loaded_data.pop(0)
    params = []
    for s in loaded_data:
        r = s.split('| ')
        t = r[len(r) - 1]
        res = [x for x in t.split('\t')]
        res = res[:len(res)-1]
        res = [float(x) for x in res]
        params.append(res)
    return params

In [145]:
sp_lines = {'sp=0.25':dict(color='#440154', width=2, dash='solid'),
        'sp=0.5':dict(color='#440154', width=2, dash='dash'),                  
        'sp=0.75':dict(color='#26828e', width=2, dash='solid'),
        'sp=1.0':dict(color='#26828e', width=2, dash='dash'),                  
        'sp=1.25':dict(color='#6ece58', width=2, dash='solid'),
        'sp=1.5':dict(color='#6ece58', width=2, dash='dash'),                  
        'sp=1.8':dict(color='#fde725', width=2, dash='solid'),
        'sp=2.0':dict(color='#fde725', width=2, dash='dash')}
sp_order = ['sp=0.25', 'sp=0.5','sp=0.75','sp=1.0','sp=1.25','sp=1.5','sp=1.8','sp=2.0']

sp = parse_result_data('log-17-algorithm-1 social.log')
df_sp = pd.DataFrame(sp, columns = sp_order)
fig = go.Figure()
for name in sp_order:
    fig.add_trace(go.Scatter(y=df_sp[name], name=name, line=sp_lines[name]))
apply_style_lines()
fig.show()

In [146]:
cp_lines = {'cp=0.25':dict(color='#440154', width=2, dash='solid'),
        'cp=0.5':dict(color='#440154', width=2, dash='dash'),                  
        'cp=0.75':dict(color='#26828e', width=2, dash='solid'),
        'cp=1.0':dict(color='#26828e', width=2, dash='dash'),                  
        'cp=1.25':dict(color='#6ece58', width=2, dash='solid'),
        'cp=1.5':dict(color='#6ece58', width=2, dash='dash'),                  
        'cp=1.8':dict(color='#fde725', width=2, dash='solid'),
        'cp=2.0':dict(color='#fde725', width=2, dash='dash')}
cp_order = ['cp=0.25', 'cp=0.5','cp=0.75','cp=1.0','cp=1.25','cp=1.5','cp=1.8','cp=2.0']
cp = parse_result_data('log-17-algorithm-1 cognitive.log')
df_cp = pd.DataFrame(cp, columns = cp_order)
fig = go.Figure()
for name in cp_order:
    fig.add_trace(go.Scatter(y=df_cp[name], name=name, line=cp_lines[name]))
apply_style_lines()
fig.show()

In [148]:
weight_lines = {'weight=0.5':dict(color='#440154', width=2, dash='solid'),
        'weight=0.6':dict(color='#440154', width=2, dash='dash'),                  
        'weight=0.7':dict(color='#26828e', width=2, dash='solid'),
        'weight=0.8':dict(color='#26828e', width=2, dash='dash'),                     
        'weight=0.9':dict(color='#fde725', width=2, dash='solid'),
        'weight=1.0':dict(color='#fde725', width=2, dash='dash')}
weight_order = ['weight=0.5', 'weight=0.6','weight=0.7','weight=0.8','weight=0.9','weight=1.0']

weight = parse_result_data('log-17-algorithm-1 weight.log')
df_weight = pd.DataFrame(weight, columns = weight_order)
fig = go.Figure()
for name in weight_order:
    fig.add_trace(go.Scatter(y=df_weight[name], name=name, line=weight_lines[name]))
apply_style_lines()
fig.show()

In [151]:
df_mutation

Очень низкая  Низкая  Средняя  Высокая  Очень высокая
0           0.2000  0.2000   0.2000   0.2000         0.2000
1           0.1984  0.1984   0.1984   0.1984         0.2064
2           0.2048  0.1968   0.1968   0.1968         0.2048
3           0.2032  0.1952   0.1952   0.2032         0.2032
4           0.2096  0.1936   0.1936   0.2016         0.2016
...            ...     ...      ...      ...            ...
996         0.2032  0.0500   0.5908   0.0948         0.0612
997         0.2080  0.0500   0.5892   0.0932         0.0596
998         0.2128  0.0500   0.5876   0.0916         0.0580
999         0.2112  0.0564   0.5860   0.0900         0.0564
1000        0.2176  0.0548   0.5844   0.0884         0.0548

[1001 rows x 5 columns]

In [152]:
mutation_lines = {'Очень низкая':dict(color='#440154', width=2),
        'Низкая':dict(color='#3e4989', width=2),
        'Средняя':dict(color='#1f9e89', width=2),
        'Высокая':dict(color='#6ece58', width=2),
        'Очень высокая':dict(color='#fde725', width=2)}
mutation_order = ['Очень низкая', 'Низкая','Средняя', 'Высокая', 'Очень высокая']
mutation_names = {'Очень низкая':'Very low', 'Низкая':'Low','Средняя':'Middle', 
                  'Высокая':'High', 'Очень высокая':'Very high'}

mutation = parse_result_data('log-20-algorithm-2 AdaptiveRGA mutation.log')
df_mutation = pd.DataFrame(mutation, columns = mutation_order)
fig = go.Figure()
for name in mutation_order:
    fig.add_trace(go.Scatter(y=df_mutation[name], name=mutation_names[name], line=mutation_lines[name]))
apply_style_lines()
fig.show()

In [153]:
recombination_lines = {'Равномерное':dict(color='#440154', width=2),
        'Одноточечное':dict(color='#1f9e89', width=2),
        'Двухточечное':dict(color='#6ece58', width=2)}
recombination_order = ['Равномерное', 'Одноточечное','Двухточечное']
recombination_names = {'Равномерное':'Uniform', 'Одноточечное':'One-point','Двухточечное':'Two-point'}

recombination = parse_result_data('log-20-algorithm-2 AdaptiveRGA recombination.log')
df_recombination = pd.DataFrame(recombination, columns = recombination_order)
fig = go.Figure()
for name in recombination_order:
    fig.add_trace(go.Scatter(y=df_recombination[name], name=recombination_names[name], line=recombination_lines[name]))
apply_style_lines()
fig.show()

In [154]:
width = 2
selection_lines = {'Турнирная 2':dict(color='#440154', width=width, dash='solid'),
        'Турнирная 4':dict(color='#440154', width=width, dash='dash'),
                  
        'Турнирная 8':dict(color='#26828e', width=width, dash='solid'),
        'Пропорциональная':dict(color='#26828e', width=width, dash='dash'),
                  
        'Ранговая линейная':dict(color='#6ece58', width=width, dash='solid'),
        'Ранговая эксп 0.8':dict(color='#6ece58', width=width, dash='dash'),
                  
        'Ранговая эксп 0.9':dict(color='#fde725', width=width, dash='solid'),
        'Ранговая эксп 0.95':dict(color='#fde725', width=width, dash='dash')}
selection_order = ['Турнирная 2', 'Турнирная 4','Турнирная 8','Пропорциональная',
                 'Ранговая линейная','Ранговая эксп 0.8','Ранговая эксп 0.9','Ранговая эксп 0.95']
selection_names = {'Турнирная 2':'Tournament 2', 'Турнирная 4':'Tournament 4','Турнирная 8':'Tournament 8',
                   'Пропорциональная':'Proporsional', 'Ранговая линейная':'Rank linear',
                   'Ранговая эксп 0.95':'Rank exp 0.95','Ранговая эксп 0.9':'Rank exp 0.9',
                   'Ранговая эксп 0.8':'Rank exp 0.8'}

selection = parse_result_data('log-20-algorithm-2 AdaptiveRGA selection.log')
df_selection = pd.DataFrame(selection, columns = selection_order)
fig = go.Figure()
for name in selection_order:
    fig.add_trace(go.Scatter(y=df_selection[name], name=selection_names[name], line=selection_lines[name]))
apply_style_lines()
fig.show()

In [155]:
cc_lines = {'C=0.3':dict(color='#440154', width=2),
        'C=0.5':dict(color='#3e4989', width=2),
        'C=0.7':dict(color='#1f9e89', width=2),
        'C=0.9':dict(color='#6ece58', width=2),
        'C=1.0':dict(color='#fde725', width=2)}
cc_order = ['C=0.3', 'C=0.5','C=0.7', 'C=0.9', 'C=1.0']

cc = parse_result_data('log-17-algorithm-0 CR.log')
df_cc = pd.DataFrame(cc, columns = cc_order)
fig = go.Figure()
for name in cc_order:
    fig.add_trace(go.Scatter(y=df_cc[name], name=name, line=cc_lines[name]))
apply_style_lines()
fig.show()

In [156]:
ff_lines = {'F=0.2':dict(color='#440154', width=2),
        'F=0.5':dict(color='#3e4989', width=2),
        'F=0.7':dict(color='#1f9e89', width=2),
        'F=1.0':dict(color='#6ece58', width=2),
        'F=1.5':dict(color='#fde725', width=2)}
ff_order = ['F=0.2', 'F=0.5','F=0.7', 'F=1.0', 'F=1.5']

ff = parse_result_data('log-17-algorithm-0 FF.log')
df_ff = pd.DataFrame(ff, columns = ff_order)
fig = go.Figure()
for name in ff_order:
    fig.add_trace(go.Scatter(y=df_ff[name], name=name, line=ff_lines[name]))
apply_style_lines()
fig.show()

In [158]:
de_type_lines = {'3 случайных вектора':dict(color='#440154', width=2),
        'Лучший вектор':dict(color='#6ece58', width=2)}
de_type_order = ['3 случайных вектора', 'Лучший вектор']
de_type_names = {'3 случайных вектора':'3 random vectors', 'Лучший вектор':'Best vector'}

de_types = parse_result_data('log-17-algorithm-0 deType.log')
df_de_type = pd.DataFrame(de_types, columns = de_type_order)
fig = go.Figure()
for name in de_type_order:
    fig.add_trace(go.Scatter(y=df_de_type[name], name=de_type_names[name], line=de_type_lines[name]))
apply_style_lines()
fig.show()

In [159]:
lymbda_lines = {'l=0.2':dict(color='#440154', width=2),
        'l=0.5':dict(color='#3e4989', width=2),
        'l=0.7':dict(color='#1f9e89', width=2),
        'l=1.0':dict(color='#6ece58', width=2),
        'l=1.5':dict(color='#fde725', width=2)}
lymbda_order = ['l=0.2', 'l=0.5','l=0.7', 'l=1.0', 'l=1.5']

lymbda = parse_result_data('log-17-algorithm-0 lymbda.log')
df_lymbda = pd.DataFrame(lymbda, columns = lymbda_order)
fig = go.Figure()
for name in lymbda_order:
    fig.add_trace(go.Scatter(y=df_lymbda[name], name=name, line=lymbda_lines[name]))
apply_style_lines()
fig.show()

In [135]:
sccc_lines = {'ScPSO':dict(color='#440154', width=2),
        'ScRGA':dict(color='#1f9e89', width=2),
        'ScDE':dict(color='#fde725', width=2)}
sccc_order = ['ScPSO', 'ScRGA', 'ScDE']
sccc_data = []
sccc_names = ['ScRGA', 'ScDE', 'ScPSO']
file = path + "\\" + 'populationsize3.log'
problem='Problem 22'
loaded_data = load(file)
sccc = []
for s in loaded_data:
    r = s.split('| ')
    t = r[len(r) - 1]
    res = [x for x in t.split('\t')]
    res = res[:len(res)-1]
    res = [float(x) for x in res]
    sccc.append(res)
df_sccc = pd.DataFrame(sccc, columns = sccc_names)
df_sccc.reset_index(inplace=True)
df_sccc['index'] = df_sccc['index'] * 10
fig = go.Figure()
for name in sccc_order:
    fig.add_trace(go.Scatter(y=df_sccc[name], x=df_sccc['index'],name=name, line=sccc_lines[name]))
fig.update_layout(autosize=False, width=800, height=500, xaxis_title="Iteration", yaxis_title="Population size")
fig.update_layout(title={'text': problem, 'x':0.5, 'y':0.87})
apply_style_lines()
fig.show()

In [137]:
fig = go.Figure()
width=3
df = pd.DataFrame.from_dict(mean_data, orient='index')
fig.add_traces(go.Scatter(y=df['PSO'], mode = 'lines+markers', name="PSO", 
                          line=dict(color='#440154', width=width, dash='dot'),
                          marker=dict(symbol="x", size=9)))
fig.add_traces(go.Scatter(y=df['ScPSO'], mode = 'lines+markers', name="ScPSO", 
                          line=dict(color='#440154', width=width, dash='longdash'),
                          marker=dict(symbol="x", size=9)))
fig.add_traces(go.Scatter(y=df['RGA'], mode = 'lines+markers', name="RGA", 
                          line=dict(color='#26828e', width=width, dash='dot'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['ScRGA'], mode = 'lines+markers', name="ScRGA", 
                          line=dict(color='#26828e', width=width, dash='longdash'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['DE'], mode = 'lines+markers', name="DE", 
                          line=dict(color='#6ece58', width=width, dash='dot'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScDE'], mode = 'lines+markers', name="ScDE", 
                          line=dict(color='#6ece58', width=width, dash='longdash'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal SBSP'], mode = 'lines+markers', name="ScCCreal SBSP", 
                          line=dict(color='#fde725', width=width),
                          marker=dict(symbol="circle", size=7)))
apply_style_lines(width=900, height=450, xaxis_title="Problem", yaxis_title="Reliability")
fig.show()

In [138]:
fig = go.Figure()
width=3
df = pd.DataFrame.from_dict(mean_data, orient='index')
fig.add_traces(go.Scatter(y=df['PSO'], mode = 'lines+markers', name="PSO", 
                          line=dict(color='#dee2e6', width=width, dash='dot'),
                          marker=dict(symbol="x", size=7)))
fig.add_traces(go.Scatter(y=df['ScPSO'], mode = 'lines+markers', name="ScPSO", 
                          line=dict(color='#dee2e6', width=width, dash='longdash'),
                          marker=dict(symbol="x", size=7)))
fig.add_traces(go.Scatter(y=df['RGA'], mode = 'lines+markers', name="RGA", 
                          line=dict(color='#adb5bd', width=width, dash='dot'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['ScRGA'], mode = 'lines+markers', name="ScRGA", 
                          line=dict(color='#adb5bd', width=width, dash='longdash'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['DE'], mode = 'lines+markers', name="DE", 
                          line=dict(color='#6c757d', width=width, dash='dot'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScDE'], mode = 'lines+markers', name="ScDE", 
                          line=dict(color='#6c757d', width=width, dash='longdash'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal SBSP'], mode = 'lines+markers', name="ScCCreal<br>SBSP", 
                          line=dict(color='black', width=width)))
apply_style_lines(width=900, height=450, xaxis_title="Problem", yaxis_title="Reliability")
fig.show()

In [139]:
fig = go.Figure()
width=3
df = pd.DataFrame.from_dict(mean_data, orient='index')
df_best = pd.DataFrame.from_dict(best_data, orient='index')
fig.add_traces(go.Scatter(y=df['DE'], mode = 'lines+markers', name="DE", 
                          line=dict(color='#fde725', width=width),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df_best['DE'], mode = 'lines+markers', name="DE best", 
                          line=dict(color='#fde725', width=width, dash='longdash'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['RGA'], mode = 'lines+markers', name="RGA", 
                          line=dict(color='#6ece58', width=width),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df_best['RGA'], mode = 'lines+markers', name="RGA best", 
                          line=dict(color='#6ece58', width=width, dash='longdash'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['PSO'], mode = 'lines+markers', name="PSO", 
                          line=dict(color='#440154', width=width),
                          marker=dict(symbol="circle", size=7)))
fig.add_traces(go.Scatter(y=df_best['PSO'], mode = 'lines+markers', name="PSO best", 
                          line=dict(color='#440154', width=width, dash='longdash'),
                          marker=dict(symbol="circle", size=7)))
apply_style_lines(width=900, height=450, xaxis_title="Problem", yaxis_title="Reliability")
fig.show()

In [140]:
fig = go.Figure()
width=3
df = pd.DataFrame.from_dict(mean_data, orient='index')
df_best = pd.DataFrame.from_dict(best_data, orient='index')
fig.add_traces(go.Scatter(y=df['DE'], mode = 'lines+markers', name="DE", 
                          line=dict(color='#ced4da', width=width),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df_best['DE'], mode = 'lines+markers', name="DE best", 
                          line=dict(color='#ced4da', width=width, dash='longdash'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['RGA'], mode = 'lines+markers', name="RGA", 
                          line=dict(color='#6c757d', width=width),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df_best['RGA'], mode = 'lines+markers', name="RGA best", 
                          line=dict(color='#6c757d', width=width, dash='longdash'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['PSO'], mode = 'lines+markers', name="PSO", 
                          line=dict(color='black', width=width),
                          marker=dict(symbol="circle", size=7)))
fig.add_traces(go.Scatter(y=df_best['PSO'], mode = 'lines+markers', name="PSO best", 
                          line=dict(color='black', width=width, dash='longdash'),
                          marker=dict(symbol="circle", size=7)))
apply_style_lines(width=900, height=450, xaxis_title="Problem", yaxis_title="Reliability")
fig.show()

In [141]:
fig = go.Figure()
width=2
df = pd.DataFrame.from_dict(mean_data, orient='index')
fig.add_traces(go.Scatter(y=df['ScCCreal AtA BrR'], mode = 'lines+markers', name="ScCCreal AtA BrR", 
                          line=dict(color='#440154', width=width, dash='dot'),
                          marker=dict(symbol="x", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal AtA BrW'], mode = 'lines+markers', name="ScCCreal AtA BrW", 
                          line=dict(color='#440154', width=width, dash='longdash'),
                          marker=dict(symbol="x", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal AtA RrR'], mode = 'lines+markers', name="ScCCreal AtA RrR", 
                          line=dict(color='#3e4989', width=width, dash='dot'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['ScCCreal AtA RrW'], mode = 'lines+markers', name="ScCCreal AtA RrW", 
                          line=dict(color='#3e4989', width=width, dash='longdash'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA BrR'], mode = 'lines+markers', name="ScCCreal BtA BrR", 
                          line=dict(color='#1f9e89', width=width, dash='dot'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA BrW'], mode = 'lines+markers', name="ScCCreal BtA BrW", 
                          line=dict(color='#1f9e89', width=width, dash='longdash'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA RrR'], mode = 'lines+markers', name="ScCCreal BtA RrR", 
                          line=dict(color='#6ece58', width=width, dash='dot'),
                          marker=dict(symbol="arrow-left", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA RrW'], mode = 'lines+markers', name="ScCCreal BtA RrW", 
                          line=dict(color='#6ece58', width=width, dash='longdash'),
                          marker=dict(symbol="arrow-left", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal SBSP'], mode = 'lines+markers', name="ScCCreal SBSP", 
                          line=dict(color='#fde725', width=width),
                          marker=dict(symbol="circle", size=7)))
apply_style_lines(width=900, height=450, xaxis_title="Problem", yaxis_title="Reliability")
fig.show()

In [142]:
fig = go.Figure()
width=2
df = pd.DataFrame.from_dict(mean_data, orient='index')
fig.add_traces(go.Scatter(y=df['ScCCreal AtA BrR'], mode = 'lines+markers', name="ScCCreal AtA BrR", 
                          line=dict(color='#ced4da', width=width, dash='dot'),
                          marker=dict(symbol="x", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal AtA BrW'], mode = 'lines+markers', name="ScCCreal AtA BrW", 
                          line=dict(color='#ced4da', width=width, dash='longdash'),
                          marker=dict(symbol="x", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal AtA RrR'], mode = 'lines+markers', name="ScCCreal AtA RrR", 
                          line=dict(color='#adb5bd', width=width, dash='dot'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['ScCCreal AtA RrW'], mode = 'lines+markers', name="ScCCreal AtA RrW", 
                          line=dict(color='#adb5bd', width=width, dash='longdash'),
                          marker=dict(symbol="square", size=7)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA BrR'], mode = 'lines+markers', name="ScCCreal BtA BrR", 
                          line=dict(color='#6c757d', width=width, dash='dot'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA BrW'], mode = 'lines+markers', name="ScCCreal BtA BrW", 
                          line=dict(color='#6c757d', width=width, dash='longdash'),
                          marker=dict(symbol="star", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA RrR'], mode = 'lines+markers', name="ScCCreal BtA RrR", 
                          line=dict(color='#495057', width=width, dash='dot'),
                          marker=dict(symbol="arrow-left", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal BtA RrW'], mode = 'lines+markers', name="ScCCreal BtA RrW", 
                          line=dict(color='#495057', width=width, dash='longdash'),
                          marker=dict(symbol="arrow-left", size=9)))
fig.add_traces(go.Scatter(y=df['ScCCreal SBSP'], mode = 'lines+markers', name="ScCCreal SBSP", 
                          line=dict(color='black', width=3),
                          marker=dict(symbol="circle", size=7)))
apply_style_lines(width=900, height=450, xaxis_title="Problem", yaxis_title="Reliability")
fig.show()